In [1]:
import adaptive
adaptive.notebook_extension()

import numpy as np
from functools import partial
import random

In [2]:
offset = random.uniform(-0.5, 0.5)

def f(x, offset=offset, wait=True):
    from time import sleep
    from random import random

    a = 0.01
    if wait:
        sleep(random() / 10)
    return x + a**2 / (a**2 + (x - offset)**2)

In [3]:
learner = adaptive.Learner1D(f, bounds=(-1, 1))

In [4]:
# The end condition is when the "loss" is less than 0.1. In the context of the
# 1D learner this means that we will resolve features in 'func' with width 0.1 or wider.
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

In [5]:
await runner.task  # This is not needed in a notebook environment!

In [6]:
runner.live_info()

In [7]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I :Scatter   [x]   (y)

In [8]:
if not runner.task.done():
    raise RuntimeError('Wait for the runner to finish before executing the cells below!')

In [9]:
learner2 = adaptive.Learner1D(f, bounds=learner.bounds)

xs = np.linspace(*learner.bounds, len(learner.data))
learner2.tell_many(xs, map(partial(f, wait=False), xs))

learner.plot() + learner2.plot()

:Layout
   .Overlay.I  :Overlay
      .Scatter.I :Scatter   [x]   (y)
   .Overlay.II :Overlay
      .Scatter.I :Scatter   [x]   (y)

In [10]:
random.seed(0)
offsets = [random.uniform(-0.8, 0.8) for _ in range(3)]

# sharp peaks at random locations in the domain
def f_levels(x, offsets=offsets):
    a = 0.01
    return np.array([offset + x + a**2 / (a**2 + (x - offset)**2)
                     for offset in offsets])

In [11]:
learner = adaptive.Learner1D(f_levels, bounds=(-1, 1))
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

In [12]:
await runner.task  # This is not needed in a notebook environment!

/home/docs/checkouts/readthedocs.org/user_builds/adaptive/conda/v0.13.0/lib/python3.9/site-packages/numpy/core/fromnumeric.py:86: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)


In [13]:
runner.live_info()

In [14]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I   :Scatter   [x]   (y)
      .Scatter.II  :Scatter   [x]   (y)
      .Scatter.III :Scatter   [x]   (y)

In [15]:
from adaptive.learner.learner1D import (curvature_loss_function,
                                        uniform_loss,
                                        default_loss)
curvature_loss = curvature_loss_function()
learner = adaptive.Learner1D(f, bounds=(-1, 1), loss_per_interval=curvature_loss)
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

In [16]:
await runner.task  # This is not needed in a notebook environment!

In [17]:
runner.live_info()

In [18]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I :Scatter   [x]   (y)

In [19]:
def sin_exp(x):
    from math import exp, sin
    return sin(15 * x) * exp(-x**2*2)

learner_h = adaptive.Learner1D(sin_exp, (-1, 1), loss_per_interval=uniform_loss)
learner_1 = adaptive.Learner1D(sin_exp, (-1, 1), loss_per_interval=default_loss)
learner_2 = adaptive.Learner1D(sin_exp, (-1, 1), loss_per_interval=curvature_loss)

npoints_goal = lambda l: l.npoints >= 100
# adaptive.runner.simple is a non parallel blocking runner.
adaptive.runner.simple(learner_h, goal=npoints_goal)
adaptive.runner.simple(learner_1, goal=npoints_goal)
adaptive.runner.simple(learner_2, goal=npoints_goal)

(learner_h.plot().relabel('homogeneous')
 + learner_1.plot().relabel('euclidean loss')
 + learner_2.plot().relabel('curvature loss')).cols(2)

:Layout
   .Overlay.Homogeneous    :Overlay
      .Scatter.I :Scatter   [x]   (y)
   .Overlay.Euclidean_loss :Overlay
      .Scatter.I :Scatter   [x]   (y)
   .Overlay.Curvature_loss :Overlay
      .Scatter.I :Scatter   [x]   (y)